In [1]:
# coding: utf-8
import ast
import os
import sys
import re
from pprint import pprint
import numpy as np
from tqdm import tqdm
import matplotlib.pyplot as plt


from func import simulation as sim

##############################################
# Monte-Carlo simulation of BFG-Y2H screen   #
# Initially developped by Nozomu Yachie      #
# Last modified by Daniel Evans-Yamamoto     #
##############################################

run_name = "test"

In [2]:
# Define teh number of strains here;
x_strain_num = 500
y_strain_num = 500

In [3]:
# Setting haploid population
x_hap = [["x_%4d"%(i+1),1] for i in range(x_strain_num)]
y_hap = [["y_%4d"%(i+1),1] for i in range(y_strain_num)]

In [4]:
hap_size = 10 * 3*10**7; # 1 OD unit of haploid cells = 3 x 10^7 


# Adjusting the cell number of each strain in pool.
x_hap = sim.adjust_num(x_hap,0.3,hap_size)
y_hap = sim.adjust_num(y_hap,0.3,hap_size)
    
cov = sim.hap_coverage(x_hap,y_hap,run_name)


In [5]:
print("The ratio of strains having at lesat the number of cells above threshold.")
print("Cells per haploid pool: %d OD600nm units"%(hap_size/(3*10**7)))
sim.print_LL(cov)

The ratio of strains having at lesat the number of cells above threshold.
Cells per haploid pool: 10 OD600nm units
Threashold	x_percentage	y_percentage
1        	100.0    	100.0    
10       	100.0    	100.0    
100      	100.0    	100.0    
1000     	100.0    	100.0    
10000    	100.0    	100.0    
100000   	99.8     	100.0    
1000000  	3.8      	3.8      
10000000 	0.0      	0.0      


In [6]:
# Simulating diploid cells after en masse yeast mating subjected for diploid selection

mating_efficacy   = 0.01 # This is underestimation to be safe.
diploid_selection = 500 * 3 * 10**7 # Amount of cells to be selected for diploids.
est_diploids      = diploid_selection*mating_efficacy

dip = sim.mating(x_hap,y_hap)
dip = sim.adjust_num(dip,0.5,est_diploids)#CV of X-Y pair-dependent mating efficiencies (log-normal distribution) is 50%
cov = sim.dip_coverage(dip,run_name)


print("The ratio of diploid strains having at least the number of cells above threshold.")
sim.print_LL(cov)

#If you want to estimate the optimal paramater for coverage, create a for loop with the variable, and plot a line plot.

The ratio of diploid strains having at least the number of cells above threshold.
Threashold	Percentage
1       	100.0   
10      	99.99   
100     	98.62   
1000    	9.98    
10000   	0.05    
100000  	0.0     
1000000 	0.0     


In [7]:
###############################################################
# Diploid selection and amount of cells spread per plate


# Amount of cells to be spread to each selection plate
dip_plate = 50 * 1.0 * 10**7 #1 OD(600 nm) unit for diploid yeast is 1 × 10^7 cells ml^-1
###############################################################################################################
### !!!! After observing CFUs on the plates, update dip_plate to check if the CFU is enough down stream !!  ###
###############################################################################################################

dip = sim.adjust_num(dip,0.5,dip_plate) #CV of X-Y pair-dependent growth amplitudes (log-normal distribution) in liquid media is 50%


In [8]:
#pprint(dip)

In [9]:
cells_for_dox_induction = 25 * 1.0 * 10**7
dip_neg = sim.adjust_num(dip,0.1,cells_for_dox_induction) #CV of X-Y pair-dependent growth amplitudes (log-normal distribution) in non-selectable condition is 10%

pos_rate  = 0.001 #PPI ositive rate is 0.1% (overestimation)
CV_autoactivity = 0.1 # Log CV for autoactivity in BFG-PCA is 10% for each of DHFR12 and DHFR3. It was 300% for DB and 60% for AD in BFG-Y2H. DB
dip_pos = sim.positive_interaction(dip,0.10,CV_autoactivity,pos_rate,cells_for_dox_induction) #CV of X-Y pair-dependent growth amplitudes (log-normal distribution) in BFG-PCA-selectable condition is 10%



In [10]:
# Examine the coverage for diploids 
cov_pos = sim.dip_coverage(dip_pos,run_name)
cov_pos_ppi = sim.dip_coverage([strain for strain in dip_pos if (strain[0][2]==1)],run_name)
cov_neg = sim.dip_coverage(dip_neg,run_name)

print("The ratio of diploid strains having at least the number of cells carried over to next step above threshold.")
print("\nNon-selection:")
sim.print_LL(cov_neg)

print("\nSelection :")
sim.print_LL(cov_pos)

print("\nCoverage of strains with positives PPIs in selectable condition")
sim.print_LL(cov_pos_ppi)

The ratio of diploid strains having at least the number of cells carried over to next step above threshold.

Non-selection:
Threashold	Percentage
1       	100.0   
10      	99.99   
100     	98.56   
1000    	29.39   
10000   	0.34    
100000  	0.0     
1000000 	0.0     

Selection :
Threashold	Percentage
1       	100.0   
10      	99.99   
100     	98.56   
1000    	29.39   
10000   	0.34    
100000  	0.0     
1000000 	0.0     

Coverage of strains with positives PPIs in selectable condition
Threashold	Percentage
1       	100.0   
10      	100.0   
100     	100.0   
1000    	100.0   
10000   	100.0   
100000  	3.2     
1000000 	0.0     


In [11]:
# You will be able to plot a heatmap of abundance at this stage.

In [12]:
###################################################
# Plasmid prep


plasmid_molecules = 1.4 * 10**7 #See below for estimation

###################################################
# Molecule estimation when performing 4 PCR reactions after plasmid prep;
#
# 100 pg / µL * 16  µL * 4 reactions = 6400 pg
# Fraction of Y2H plasmids in yeast DNA miniprep product is 6% of the total DNA mass
# Barcode fusion efficiency is 20%
# 6400 pg * 0.06 * 0.2  = 152.6 pg
# Y2H plasmid sizes are 10 kbp
# 1 mole of double-stranded DNA molecule is 660 g bp^-1 (1ng = 0.152 fmol)
# 153.6 * (1/1000 * 0.152) fmol  = 153.6 * 10**-3 * 0.152 * 10**-15 * 6.03* 10**23
#                                = 153.6 * 6.03 * 0.152 * 10**5
#                                = 1.4 * 10**7 molecules
######################################################


plasmid_neg = sim.adjust_num(dip_neg,0.5,plasmid_molecules)
plasmid_pos = sim.adjust_num(dip_pos,0.5,plasmid_molecules)


In [13]:
###############################################################
# PCR re-amplification and Illumina sequencing

reads_per_condition = 2* 10**6 # Reads for each condition (add Barcode Fusion type (BC1-BC1 or BC2-BC2) in each condition.)


read_neg = sim.adjust_num(plasmid_neg,0.5,reads_per_condition)
read_pos = sim.adjust_num(plasmid_pos,0.5,reads_per_condition)
read_pos_PPI = sim.adjust_num([strain for strain in read_pos if (strain[0][2]==1)],0.5,reads_per_condition)



In [14]:
# Examining coverage at final output
cov_pos = sim.dip_coverage(read_pos,run_name)
cov_pos_ppi = sim.dip_coverage([strain for strain in read_pos if (strain[0][2]==1)],run_name)
cov_neg = sim.dip_coverage(read_neg,run_name)

print("The ratio of diploid strains having at least the number of reads sequenced.")
print("\nNon-selection:")
sim.print_LL(cov_neg)

print("\nSelection :")
sim.print_LL(cov_pos)

print("\nCoverage of strains with positives PPIs in selectable condition")
sim.print_LL(cov_pos_ppi)

The ratio of diploid strains having at least the number of reads sequenced.

Non-selection:
Threashold	Percentage
1       	84.78   
10      	17.54   
100     	0.66    
1000    	0.1     
10000   	0.02    
100000  	0.0     
1000000 	0.0     

Selection :
Threashold	Percentage
1       	84.78   
10      	17.54   
100     	0.66    
1000    	0.1     
10000   	0.02    
100000  	0.0     
1000000 	0.0     

Coverage of strains with positives PPIs in selectable condition
Threashold	Percentage
1       	100.0   
10      	100.0   
100     	100.0   
1000    	90.0    
10000   	19.6    
100000  	0.8     
1000000 	0.0     


In [16]:
# Plot histogram to compare with obtained data.

# Haploid abundance histogram
marginal_x_hap,marginal_y_hap = sim.marginal(read_neg)
# Diploid abundance histogram
abundance_pos                 = sim.abundance(read_neg)
abundance_neg                 = sim.abundance(read_pos)

# Function to format array data for heatmap representation in each condition 
hmap_read_neg = sim.format_array(read_neg)

[['x', 'y', 'value'],
 ['x_  20', 'y_ 307', 40216.6749368654],
 ['x_ 419', 'y_ 197', 21929.60662545835],
 ['x_ 120', 'y_ 412', 25051.92886256915],
 ['x_ 461', 'y_  99', 181389.66266698382],
 ['x_ 272', 'y_ 364', 20626.913289406722],
 ['x_ 223', 'y_  33', 31626.12346191212],
 ['x_ 177', 'y_ 333', 5586.899359166691],
 ['x_  64', 'y_ 248', 10765.3688326627],
 ['x_  97', 'y_ 387', 9401.501011972077],
 ['x_ 158', 'y_ 389', 18374.285765316967],
 ['x_ 169', 'y_  33', 12264.187812741897],
 ['x_ 307', 'y_ 107', 15576.737354641004],
 ['x_ 496', 'y_ 258', 10588.939770716212],
 ['x_ 456', 'y_  80', 12268.186785762751],
 ['x_ 259', 'y_  19', 13374.79551417891],
 ['x_  51', 'y_ 299', 6056.523223487189],
 ['x_  28', 'y_ 405', 1908.7614589329473],
 ['x_  33', 'y_  17', 9782.102573686481],
 ['x_ 419', 'y_ 310', 2127.323756634654],
 ['x_ 401', 'y_ 166', 2412.3631995239857],
 ['x_ 475', 'y_ 145', 4124.376832005148],
 ['x_ 205', 'y_ 154', 1974.8433055424584],
 ['x_ 431', 'y_ 399', 957.1858138688592],
 ['x

 ['x_ 496', 'y_ 142', 28.437318027541433],
 ['x_  18', 'y_ 448', 14.205921518925816],
 ['x_ 313', 'y_ 450', 84.5366888980315],
 ['x_ 172', 'y_   2', 188.02983622806485],
 ['x_  10', 'y_ 434', 53.21577399615045],
 ['x_ 233', 'y_ 214', 37.71461218864416],
 ['x_ 180', 'y_ 122', 13.457719701168267],
 ['x_ 452', 'y_  90', 25.663587334157302],
 ['x_ 356', 'y_  78', 11.966334671660476],
 ['x_ 431', 'y_ 401', 26.73313060877929],
 ['x_  54', 'y_ 341', 2.6797505443207927],
 ['x_ 496', 'y_   4', 12.986371697464719],
 ['x_ 431', 'y_ 112', 7.805167717322997],
 ['x_ 223', 'y_ 437', 17.182386201902784],
 ['x_ 252', 'y_ 197', 26.223308075069625],
 ['x_   7', 'y_  33', 11.723556364001542],
 ['x_ 415', 'y_ 265', 62.741256777949346],
 ['x_ 496', 'y_ 293', 28.959934901990245],
 ['x_ 374', 'y_ 438', 26.131710597197515],
 ['x_  33', 'y_ 165', 9.58758650106765],
 ['x_ 242', 'y_ 310', 10.225565450348817],
 ['x_ 238', 'y_   3', 54.8160897596528],
 ['x_ 314', 'y_ 250', 16.234072989187574],
 ['x_ 199', 'y_  37',

 ['x_ 242', 'y_ 497', 55.59251748215533],
 ['x_ 181', 'y_ 445', 7.241607017099724],
 ['x_ 191', 'y_ 399', 28.379940156873136],
 ['x_ 223', 'y_ 253', 26.10329026073555],
 ['x_ 272', 'y_ 412', 62.4119724607309],
 ['x_ 337', 'y_  69', 12.20276498379217],
 ['x_ 370', 'y_ 293', 105.31408801474278],
 ['x_  56', 'y_ 488', 21.25816279442672],
 ['x_ 407', 'y_ 437', 137.8952658425231],
 ['x_ 116', 'y_ 190', 22.110016411597773],
 ['x_ 443', 'y_ 389', 14.270029362793027],
 ['x_ 429', 'y_ 211', 51.328752785158756],
 ['x_ 313', 'y_ 162', 31.847848117451388],
 ['x_ 401', 'y_ 412', 17.602602668881627],
 ['x_  39', 'y_ 449', 12.81312161501728],
 ['x_ 223', 'y_  86', 9.59399032319236],
 ['x_ 368', 'y_ 449', 0.8115467957120983],
 ['x_ 264', 'y_ 460', 30.67438402252763],
 ['x_ 456', 'y_ 394', 7.775024302309948],
 ['x_  27', 'y_ 197', 14.680959899665169],
 ['x_ 419', 'y_ 412', 59.22840565674318],
 ['x_ 461', 'y_ 215', 6.059973553504049],
 ['x_ 265', 'y_ 179', 6.2302610972682935],
 ['x_ 129', 'y_ 410', 29.8

 ['x_ 190', 'y_ 379', 4.629841369726511],
 ['x_ 220', 'y_ 426', 0.677600504516434],
 ['x_ 489', 'y_ 422', 52.954369219667115],
 ['x_ 388', 'y_ 345', 17.786787289449954],
 ['x_ 190', 'y_ 310', 11.34452776481684],
 ['x_ 148', 'y_  17', 21.88280236949521],
 ['x_  91', 'y_ 266', 9.204320573620066],
 ['x_ 125', 'y_ 328', 46.5947589485581],
 ['x_ 299', 'y_ 352', 8.102758176443626],
 ['x_ 277', 'y_ 354', 7.648798244179368],
 ['x_ 328', 'y_   3', 40.84278609080056],
 ['x_ 263', 'y_  50', 32.82972602960215],
 ['x_ 464', 'y_ 111', 5.523292697683122],
 ['x_ 192', 'y_ 113', 19.07454406502116],
 ['x_  87', 'y_ 187', 33.36032679267244],
 ['x_ 374', 'y_  52', 8.682235270550873],
 ['x_ 136', 'y_  81', 13.944042007392389],
 ['x_ 191', 'y_   2', 2.1796158595736688],
 ['x_ 259', 'y_ 441', 14.74136141178056],
 ['x_ 224', 'y_  78', 22.493177164185948],
 ['x_ 351', 'y_ 200', 20.231794852156334],
 ['x_  17', 'y_ 190', 13.701044340092862],
 ['x_  40', 'y_ 319', 12.51893421828478],
 ['x_ 117', 'y_ 168', 22.868

 ['x_ 283', 'y_ 128', 7.28680109509494],
 ['x_ 329', 'y_ 427', 11.701179480152787],
 ['x_ 498', 'y_ 394', 28.010314254486303],
 ['x_ 202', 'y_ 308', 68.35018807508396],
 ['x_ 189', 'y_ 197', 23.181058981741558],
 ['x_ 264', 'y_  21', 13.191751351317857],
 ['x_ 356', 'y_ 404', 140.87320531162067],
 ['x_ 232', 'y_ 182', 3.967326574773315],
 ['x_ 222', 'y_ 181', 22.127089882958344],
 ['x_ 113', 'y_ 231', 24.448037335242418],
 ['x_  50', 'y_  23', 38.83938196706288],
 ['x_  50', 'y_ 303', 17.835526750356617],
 ['x_ 356', 'y_ 262', 40.73351790067496],
 ['x_ 352', 'y_ 465', 17.77090695675344],
 ['x_ 397', 'y_ 435', 9.073370864881406],
 ['x_ 286', 'y_  16', 22.362883392369454],
 ['x_ 496', 'y_ 343', 8.923699072967334],
 ['x_ 186', 'y_  80', 15.03666738368053],
 ['x_ 202', 'y_ 217', 8.091916455219085],
 ['x_ 283', 'y_  35', 14.455261388468022],
 ['x_ 356', 'y_ 326', 4.785840031483196],
 ['x_ 159', 'y_ 214', 60.481329521042674],
 ['x_ 411', 'y_ 321', 12.5131529706839],
 ['x_ 408', 'y_  17', 16.

...

 ['x_ 190', 'y_ 135', 4.061009338496969],
 ['x_ 245', 'y_ 109', 26.99378628581376],
 ['x_ 494', 'y_ 130', 1.0789697627389594],
 ['x_ 408', 'y_ 351', 4.159923404902379],
 ['x_ 293', 'y_ 113', 1.2965634516984592],
 ['x_ 475', 'y_ 442', 3.0402945770859664],
 ['x_ 475', 'y_ 319', 0.6586676185329888],
 ['x_ 209', 'y_ 149', 3.725400328141043],
 ['x_ 242', 'y_ 398', 11.767684600283337],
 ['x_   9', 'y_ 212', 4.90465977448172],
 ['x_  41', 'y_ 122', 2.690473044605645],
 ['x_ 402', 'y_ 308', 12.219248797855629],
 ['x_ 411', 'y_ 454', 3.074420168372984],
 ['x_ 106', 'y_ 456', 3.6848934428635602],
 ['x_ 500', 'y_ 464', 5.542115203387559],
 ['x_ 257', 'y_ 346', 2.326759486813956],
 ['x_ 457', 'y_  97', 23.961776388584124],
 ['x_ 470', 'y_ 124', 2.8034481933386903],
 ['x_ 127', 'y_ 415', 0.23902908911307313],
 ['x_  60', 'y_ 305', 0.6930217416560449],
 ['x_ 430', 'y_ 233', 38.05589452641342],
 ['x_ 411', 'y_ 221', 41.998566428630234],
 ['x_ 399', 'y_ 473', 5.073995201242275],
 ['x_ 209', 'y_ 471', 

 ['x_ 474', 'y_ 230', 5.227368241743431],
 ['x_ 410', 'y_ 289', 1.490739020765547],
 ['x_ 356', 'y_ 344', 6.474834360315633],
 ['x_ 113', 'y_ 191', 4.025843112035919],
 ['x_ 224', 'y_ 267', 1.2338029023491892],
 ['x_ 267', 'y_  77', 5.04059170011889],
 ['x_  66', 'y_  96', 3.6340098516779467],
 ['x_ 314', 'y_ 411', 5.350336095299544],
 ['x_ 482', 'y_ 199', 3.647468517181046],
 ['x_ 323', 'y_  94', 2.6517411202375247],
 ['x_ 448', 'y_ 230', 1.7228051419137786],
 ['x_ 369', 'y_ 228', 0.9975548373049746],
 ['x_  88', 'y_ 312', 19.204076048110263],
 ['x_ 377', 'y_ 486', 2.691493745657297],
 ['x_ 400', 'y_ 160', 6.346495363923485],
 ['x_ 163', 'y_ 457', 5.10689782647586],
 ['x_ 490', 'y_  28', 1.0943872009596312],
 ['x_ 199', 'y_ 326', 4.5004965306135025],
 ['x_ 245', 'y_  28', 4.077806145756275],
 ['x_ 314', 'y_ 289', 1.8037477025349622],
 ['x_ 204', 'y_ 200', 2.5668448782593067],
 ['x_  97', 'y_ 158', 0.7593427571237878],
 ['x_ 306', 'y_ 400', 2.4811358527857186],
 ['x_ 414', 'y_   3', 39

 ['x_ 264', 'y_ 182', 4.781171306077005],
 ['x_ 267', 'y_ 371', 2.5279495767912863],
 ['x_ 395', 'y_ 198', 7.442254614624269],
 ['x_ 487', 'y_ 462', 5.566295961140133],
 ['x_ 266', 'y_  44', 5.132884008628272],
 ['x_  73', 'y_ 314', 1.4117437810547968],
 ['x_   8', 'y_ 190', 2.09265174246499],
 ['x_ 229', 'y_ 237', 4.182008988832681],
 ['x_ 457', 'y_ 408', 6.515195571260172],
 ['x_  83', 'y_ 209', 1.7627904141675668],
 ['x_ 146', 'y_ 261', 6.8887709930075305],
 ['x_ 330', 'y_ 378', 17.086072437414952],
 ['x_  14', 'y_ 138', 3.8428786346957544],
 ['x_ 131', 'y_ 438', 7.827209271801481],
 ['x_ 485', 'y_  79', 3.279270181675533],
 ['x_  42', 'y_ 395', 33.49966807697139],
 ['x_ 452', 'y_ 428', 5.429338947853863],
 ['x_ 363', 'y_ 217', 9.850291967218883],
 ['x_ 308', 'y_ 473', 2.678829030636759],
 ['x_ 191', 'y_  74', 1.688204848085364],
 ['x_ 250', 'y_ 451', 1.682995765218694],
 ['x_ 305', 'y_ 276', 7.88706222549744],
 ['x_ 183', 'y_  55', 1.1656779033099347],
 ['x_ 174', 'y_ 195', 4.31690

 ['x_ 112', 'y_ 240', 1.7577087248090988],
 ['x_  36', 'y_ 354', 7.439556042109355],
 ['x_ 112', 'y_   5', 2.9861097800030945],
 ['x_ 157', 'y_ 500', 1.475969485675404],
 ['x_ 454', 'y_ 132', 7.024603037284065],
 ['x_ 288', 'y_ 206', 2.240267657309476],
 ['x_ 213', 'y_  97', 3.123630657285881],
 ['x_  61', 'y_ 174', 3.4231122457767453],
 ['x_ 273', 'y_  41', 0.8754320939811698],
 ['x_ 487', 'y_ 356', 5.278721327013247],
 ['x_ 393', 'y_ 247', 9.021870779315027],
 ['x_ 126', 'y_ 469', 5.035387492216143],
 ['x_ 459', 'y_ 252', 2.6541371794952098],
 ['x_ 127', 'y_ 265', 8.959859258527636],
 ['x_ 231', 'y_ 204', 4.4708263373518795],
 ['x_ 463', 'y_ 233', 0.9772680728241727],
 ['x_ 255', 'y_ 352', 4.393062654146995],
 ['x_ 420', 'y_ 360', 26.15337642691936],
 ['x_ 312', 'y_ 499', 2.912237700540985],
 ['x_ 484', 'y_ 391', 8.15507074729374],
 ['x_ 468', 'y_ 167', 0.6647442947534079],
 ['x_ 246', 'y_ 182', 2.6049856083609524],
 ['x_ 249', 'y_ 157', 2.7052907423229975],
 ['x_ 423', 'y_ 317', 6.4

KeyboardInterrupt: 